# 03_fetch_text_at

In [1]:
# Bibliotecas

import os
import json
import pandas as pd
import requests
import re
from bs4 import BeautifulSoup

os.chdir('C:\\Users\\JVoigt\\OneDrive - Universität für Weiterbildung Krems\\Dokumente\\Python Scripts\\austrian_stenographischen_protokollen_nationalrats\\new_start_14042023')

df_speakers = pd.read_csv('df_speakers_at_final.csv', sep=";")

# limpadinha
df_speakers = df_speakers.drop(columns=['tag_politician'])

#ajustando:
def get_year(text):
    match = re.search(r'\d{4}(?=\s*\()', text)
    if match:
        year = match.group()
    else:
        year = None
    return year

def find_month(text):
    months_at = ['Jänner','Februar','März','April','Mai','Juni','Juli','August','September','Oktober','November','Dezember']
    
    for month in months_at:
        if re.search(fr'\b{month}\b', text, re.IGNORECASE):
            return month
    return None

def get_sitz(text):
    
    match = re.search(r'\((.*?)\)', text)

    if match:
        result = match.group(1).replace('/', '')
    else:
        result = None
    return result


df_speakers['year'] = df_speakers['title'].apply(get_year)
df_speakers['month'] = df_speakers['title'].apply(find_month)
df_speakers['sitzung'] = df_speakers['title'].apply(get_sitz)
df_speakers['file_title'] = ''

# nao achou nenhuma duplicata
df_speakers = df_speakers.drop_duplicates(ignore_index=True)

df_speakers.head()

index                                              title  \
0      0  207. Sitzung des Nationalrats vom 30. März 202...   
1      0  207. Sitzung des Nationalrats vom 30. März 202...   
2      0  207. Sitzung des Nationalrats vom 30. März 202...   
3      0  207. Sitzung des Nationalrats vom 30. März 202...   
4      0  207. Sitzung des Nationalrats vom 30. März 202...   

                                                 url  \
0  http://www.parlament.gv.at/gegenstand/XXVII/NR...   
1  http://www.parlament.gv.at/gegenstand/XXVII/NR...   
2  http://www.parlament.gv.at/gegenstand/XXVII/NR...   
3  http://www.parlament.gv.at/gegenstand/XXVII/NR...   
4  http://www.parlament.gv.at/gegenstand/XXVII/NR...   

                                               topic  \
0   Fragestunde mit Außenminister Alexander Schal...   
1   Fragestunde mit Außenminister Alexander Schal...   
2   Fragestunde mit Außenminister Alexander Schal...   
3   Fragestunde mit Außenminister Alexander Schal...   
4   Fragestunde mit Außenminister Alexander Schal...   

                                     name_politician  \
0      Wolfgang Sobotka, Präsident des Nationalrates   
1  Reinhold Lopatka (ÖVP) sowie Zusatzfragestelle...   
2  Katharina Kucharowits (SPÖ) sowie Zusatzfrages...   
3   Petra Steger (FPÖ) sowie ZusatzfragestellerInnen   
4  Ewa Ernst-Dziedzic (GRÜNE) sowie Zusatzfragest...   

                                          url_speech  year month    sitzung  \
0  /dokument/XXVII/NRSITZ/207/A_-_10_31_45_002931...  2023  März  207NRSITZ   
1  /dokument/XXVII/NRSITZ/207/A_-_10_32_15_002931...  2023  März  207NRSITZ   
2  /dokument/XXVII/NRSITZ/207/A_-_10_38_27_002931...  2023  März  207NRSITZ   
3  /dokument/XXVII/NRSITZ/207/A_-_10_45_27_002932...  2023  März  207NRSITZ   
4  /dokument/XXVII/NRSITZ/207/A_-_10_57_14_002932...  2023  März  207NRSITZ   

  file_title  
0             
1             
2             
3             
4

In [3]:
# Crie um objeto JSON a partir do dataframe
json_dict = df_speakers.to_dict(orient='records')

def cleaning_nome(text):
    # Apaga tudo o que vem depois do ")" ou da ", "
    text = re.sub(r'[\),].*', '', text)
    
    # Substitui todos os caracteres não permitidos por "_"
    text = re.sub(r'[^\w\s.-]', '', text)
    text = re.sub(r'[\s]', '_', text)

    return text

# Loop para pegar os textos:

for i in range(0, len(json_dict)):
        
        url_speech = json_dict[i]['url_speech']
        
        print(i, ' ', url_speech)

        try:
              # solicitando:
              url = "http://www.parlament.gv.at" + url_speech
              response = requests.get(url)

              # parse the HTML content using BeautifulSoup
              soup = BeautifulSoup(response.content, 'html.parser')

              # extract the text from the HTML code e formatando
              text = (soup.get_text()
                      .replace('\n', ' ')
                      .replace('\xa0', ' ')
                      .replace('\r', ' '))

              text = re.sub(r'\s{2,}', ' ', text)

              #criando a chave "text" e inserindo o texto
              json_dict[i]['text'] = text

              # limpando o nome para ele poder ser utilizado no file_title
              nome = cleaning_nome(str(json_dict[i]['name_politician']))

              #Chave file_title para o futuro:
              file_title = str(json_dict[i]['year']) + '_' + str(json_dict[i]['sitzung']) + '_'  + nome + '_' + str(i) + '.txt'
              json_dict[i]['file_title'] = file_title

        except requests.exceptions.RequestException as e:
              print('Erro:', e)
              continue

# Segundo o LOG, só teve 1 erro no item 5847

0   /dokument/XXVII/NRSITZ/207/A_-_10_31_45_00293172.html
1   /dokument/XXVII/NRSITZ/207/A_-_10_32_15_00293174.html
2   /dokument/XXVII/NRSITZ/207/A_-_10_38_27_00293184.html
3   /dokument/XXVII/NRSITZ/207/A_-_10_45_27_00293218.html
4   /dokument/XXVII/NRSITZ/207/A_-_10_57_14_00293201.html
5   /dokument/XXVII/NRSITZ/207/A_-_11_01_52_00293185.html
6   /dokument/XXVII/NRSITZ/207/A_-_11_06_16_00293200.html
7   /dokument/XXVII/NRSITZ/207/A_-_11_09_22_00293212.html
8   /dokument/XXVII/NRSITZ/207/A_-_11_15_16_00293197.html
9   /dokument/XXVII/NRSITZ/207/A_-_11_23_38_00293206.html
10   /dokument/XXVII/NRSITZ/207/A_-_11_29_37_00293347.html
11   /dokument/XXVII/NRSITZ/207/A_-_11_33_17_00293349.html
12   /dokument/XXVII/NRSITZ/207/A_-_11_36_57_00293355.html
13   /dokument/XXVII/NRSITZ/207/A_-_11_41_14_00293302.html
14   /dokument/XXVII/NRSITZ/207/A_-_11_47_50_00293231.html
15   /dokument/XXVII/NRSITZ/207/A_-_11_48_33_00293236.html
16   /dokument/XXVII/NRSITZ/207/A_-_11_53_44_00293211.html
17   /d

In [27]:
# # # verificando se há valores nulos em text:


df = pd.DataFrame(json_dict)
if df['text'].isna().all():
    print("A coluna 'text' está completamente vazia.")
else:
    # Verifica se existem valores vazios na coluna 'text'
    empty_values = df['text'].isin(['', None])
    if empty_values.any():
        print("A coluna 'text' contém valores vazios.")
    else:
        print("A coluna 'text' não contém valores vazios.")


## Entao ele consegue pegar todos os textos!

# Verificando se há duplicadas no nome dos textos:

duplicated_titles = df.duplicated(subset='file_title', keep=False)
print(len(duplicated_titles), len(df))

# Nao há duplicatas, eu nao sei porquê nao estava salvando

A coluna 'text' não contém valores vazios.
13938 13938


In [28]:
os.chdir('C:\\Users\\JVoigt\\OneDrive - Universität für Weiterbildung Krems\\Dokumente\\Python Scripts\\austrian_stenographischen_protokollen_nationalrats\\new_start_14042023')

# Salvando
with open('json_dict_speeches.json', "w") as arquivo:
    json.dump(json_dict, arquivo)

In [29]:
json_dict

[{'index': 0,
  'title': '207. Sitzung des Nationalrats vom 30. März 2023 (207/NRSITZ)',
  'url': 'http://www.parlament.gv.at/gegenstand/XXVII/NRSITZ/207?json=true',
  'topic': ' Fragestunde mit Außenminister Alexander Schallenberg',
  'name_politician': 'Wolfgang Sobotka, Präsident des Nationalrates',
  'url_speech': '/dokument/XXVII/NRSITZ/207/A_-_10_31_45_00293172.html',
  'year': '2023',
  'month': 'März',
  'sitzung': '207NRSITZ',
  'file_title': '2023_207NRSITZ_Wolfgang_Sobotka_0.txt',
  'text': ' Fragestunde mit Außenminister Alexander Schallenberg, 207. Sitzung, XXVII. GP des NR, 10:31 Fragestunde Präsident Mag. Wolfgang Sobotka: Wir kommen zur Fragestunde. Sie kennen den Brauch: Die Fragedauer beträgt 1 Minute, die erste Antwort, Herr Außenminister, darf 2 Minuten dauern, die Antwort auf die Zusatzfragen 1 Minute. Ich werde jeweils dezent darauf hinweisen, dass wir die Zeit einhalten. Europäische und internationale Angelegenheiten Präsident Mag. Wolfgang Sobotka: Ich darf Herr